In [1]:
import uproot
import ROOT
from ROOT import TMultiGraph, TLatex, TCanvas, TFile, TGaxis, TGraphAsymmErrors
from ROOT import gROOT, gStyle, gPad
from ROOT import TEfficiency

ROOT.gROOT.SetBatch(True)


import matplotlib.pyplot as plt
import awkward as ak
import numpy as np
from array import array
%matplotlib inline

Welcome to JupyROOT 6.28/04


In [ ]:
from collections import defaultdict

basedict = defaultdict(lambda: defaultdict(dict))

: 

In [2]:
def getEfficiencyHistoNames():
    return ["p", "pt", "phi", "eta", "nPV"]


def getTrackers(trackers):
    return trackers

#data/resolutions_and_effs_Bd2KstEE_MDmaster.root:Track/...
def getOriginFolders():
    basedict = {
        "Velo": {},
        "Upstream": {},
        "Forward": {},
        "Match": {},
        "BestLong": {},
        "Seed": {},
    }

    basedict["Velo"]["folder"] = "VeloTrackChecker/" #evtl anpassen wenn die folders anders heissen
    basedict["Upstream"]["folder"] = "UpstreamTrackChecker/"
    basedict["Forward"]["folder"] = "ForwardTrackChecker_7a0dbfa7/"
    basedict["Match"]["folder"] = "MatchTrackChecker_29e3152a/"
    basedict["BestLong"]["folder"] = "BestLongTrackChecker_4ddacce1/"
    basedict["Seed"]["folder"] = "SeedTrackChecker_1b1d5575/"

    return basedict


def getTrackNames():
    basedict = {
        "Velo": {},
        "Upstream": {},
        "Forward": {},
        "Match": {},
        "BestLong": {},
        "Seed": {},
    }

    basedict["Velo"] = "Velo"
    basedict["Upstream"] = "VeloUT"
    basedict["Forward"] = "Forward"
    basedict["Match"] = "Match"
    basedict["BestLong"] = "BestLong"
    basedict["Seed"] = "Seed"
    return basedict

trackers = ["Forward", "Match", "BestLong", "Seed"]
label = ["EffChecker"]
filename = ["/work/cetin/LHCb/stack/data/resolutions_and_effs_Bd2KstEE_MDmaster.root"]

In [3]:
def get_files(tf, filename, label):
    for i, f in enumerate(filename):
        tf[label[i]] = TFile(f, "read")
    return tf


def get_nicer_var_string(var: str):
    nice_vars = dict(pt="p_{T}", eta="#eta", phi="#phi")
    try:
        return nice_vars[var]
    except KeyError:
        return var


In [4]:
def Efficiency(numerator, denominator):
    return (numerator.GetEntries()+1.)/(denominator.GetEntries()+2.)

In [5]:
def get_eff(eff, hist, tf, histoName, label, var):
    eff = {}
    hist = {}
    var = get_nicer_var_string(var)
    for i, lab in enumerate(label):
        numeratorName = histoName + "_reconstructed"
        numerator = tf[lab].Get(numeratorName)
        denominatorName = histoName + "_reconstructible"
        denominator = tf[lab].Get(denominatorName)
        if numerator.GetEntries() == 0 or denominator.GetEntries() == 0:
            continue

        teff = Efficiency(numerator, denominator)
        #print("TBetaAlpha: "+ str(teff.GetBetaAlpha()))
        #print("TBetaBeta: "+ str(teff.GetBetaBeta()))
        eff[lab] = teff

        hist[lab] = denominator.Clone()
        hist[lab].SetName("h_numerator_notElectrons")
        hist[lab].SetTitle(var + " distribution, not e^{-}")
        if histoName.find("strange") != -1:
            hist[lab].SetTitle(var + " distribution, stranges")
        if histoName.find("electron") != -1:
            hist[lab].SetTitle(var + " distribution, e^{-}")

    return eff, hist

In [6]:
tf = {}
tf = get_files(tf, filename, label)

latex = TLatex()
latex.SetNDC()
latex.SetTextSize(0.05)

efficiencyHistoDict = efficiencyHistoDict()
efficiencyHistos = getEfficiencyHistoNames()

In [7]:


plot_electrons = False
plot_electrons_only = False

categories = categoriesDict()
cuts = getCuts()
trackers = getTrackers(trackers)
folders = getOriginFolders()
effdata = ak.ArrayBuilder()
#effdata.begin_list()
for tracker in trackers:
    effdata.begin_record()

    for cut in cuts[tracker]:
        folder = folders[tracker]["folder"]
        print(folder)
        histoBaseName = "Track/" + folder + tracker + "/" + cut + "_"


        # calculate efficiency
        for histo in efficiencyHistos:
            effdata.field(str(tracker)+"_"+str(cut)+"_"+str(histo))
            effdata.begin_list()
            canvastitle = (
                "efficiency_" + histo + ", " + categories[tracker][cut]["title"]
            )
            # get efficiency for not electrons category
            histoName = histoBaseName + "" + efficiencyHistoDict[histo]["variable"]
            print("not electrons: " + histoName)
            eff = {}
            hist_den = {}
            eff, hist_den = get_eff(eff, hist_den, tf, histoName, label, histo)

            if categories[tracker][cut]["plotElectrons"] and plot_electrons:
                histoNameElec = (
                    "Track/"
                    + folder
                    + tracker
                    + "/"
                    + categories[tracker][cut]["Electrons"]
                )
                histoName_e = (
                    histoNameElec + "_" + efficiencyHistoDict[histo]["variable"]
                )
                print("electrons: " + histoName_e)
                eff_elec = {}
                hist_elec = {}
                eff_elec, hist_elec = get_eff(eff_elec, hist_elec, tf, histoName_e, label, histo,)

            #print(type(eff))
            if not plot_electrons_only:
                effdata.append(eff[label[0]])
            if categories[tracker][cut]["plotElectrons"] and plot_electrons:
                effdata.append(eff_elec[label[0]])

            #print(eff[label[0]])
            effdata.end_list()
    effdata.end_record()

#effdata.end_list()

effdata = ak.Array(effdata)
effdata

ForwardTrackChecker_7a0dbfa7/
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/01_long_P
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/01_long_Pt
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/01_long_Phi
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/01_long_Eta
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/01_long_nPV
ForwardTrackChecker_7a0dbfa7/
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/02_long_P>5GeV_P
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/02_long_P>5GeV_Pt
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/02_long_P>5GeV_Phi
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/02_long_P>5GeV_Eta
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/02_long_P>5GeV_nPV
ForwardTrackChecker_7a0dbfa7/
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/03_long_strange_P
not electrons: Track/ForwardTrackChecker_7a0dbfa7/Forward/03_long_strange_Pt
not electrons: Track/Forward

<Array [{Forward_01_long_p: [0.872], ...}, ...] type='4 * {Forward_01_long_...'>

In [8]:
effdata.tolist()

[{'Forward_01_long_p': [0.8723027753520721],
  'Forward_01_long_pt': [0.8723027753520721],
  'Forward_01_long_phi': [0.8723027753520721],
  'Forward_01_long_eta': [0.8723027753520721],
  'Forward_01_long_nPV': [0.8723027753520721],
  'Forward_02_long_P>5GeV_p': [0.9274755004618178],
  'Forward_02_long_P>5GeV_pt': [0.9274755004618178],
  'Forward_02_long_P>5GeV_phi': [0.9274755004618178],
  'Forward_02_long_P>5GeV_eta': [0.9274755004618178],
  'Forward_02_long_P>5GeV_nPV': [0.9274755004618178],
  'Forward_03_long_strange_p': [0.7989988259848683],
  'Forward_03_long_strange_pt': [0.7989988259848683],
  'Forward_03_long_strange_phi': [0.7989988259848683],
  'Forward_03_long_strange_eta': [0.7989988259848683],
  'Forward_03_long_strange_nPV': [0.7989988259848683],
  'Forward_04_long_strange_P>5GeV_p': [0.8857386703080994],
  'Forward_04_long_strange_P>5GeV_pt': [0.8857386703080994],
  'Forward_04_long_strange_P>5GeV_phi': [0.8857386703080994],
  'Forward_04_long_strange_P>5GeV_eta': [0.885

In [78]:
arr = ak.ArrayBuilder()

for i in range(4):
    arr.begin_list()
    for j in range(5,7):
        arr.begin_record()
        for k in range(8,10):
            arr.field(str(k))
            arr.begin_list()
            arr.append(k)
            arr.end_list()
        arr.end_record()
    arr.end_list()

arr = ak.Array(arr)
arr.show()

[[{'8': [8], '9': [9]}, {'8': [8], '9': [9]}],
 [{'8': [8], '9': [9]}, {'8': [8], '9': [9]}],
 [{'8': [8], '9': [9]}, {'8': [8], '9': [9]}],
 [{'8': [8], '9': [9]}, {'8': [8], '9': [9]}]]


### try reading data

In [9]:
upFile = uproot.open("/work/cetin/LHCb/stack/data/efficiency_plots.root")
inFile = TFile.Open("/work/cetin/LHCb/stack/data/efficiency_plots.root")

In [10]:
upFile["BestLong/01_long;1"].classnames()

{'efficiency_p;1': 'TCanvas',
 'efficiency_pt;1': 'TCanvas',
 'efficiency_phi;1': 'TCanvas',
 'efficiency_eta;1': 'TCanvas',
 'efficiency_nPV;1': 'TCanvas'}

In [31]:
tree1 = inFile.Get("BestLong/01_long")
tree2 = inFile.Get("Seed/02_long")
c1 = tree1.Get("efficiency_p;1").Clone()
c2 = tree2.Get("efficiency_p;1").Clone()




AttributeError: 'bool' object has no attribute 'Get'

Error in <TDirectoryFile::Cd>: Unknown directory BestLong


In [251]:
ep = inFile.Get("BestLong/01_long/efficiency_p;1/EffChecker;2:p")
ep.Get

Canvas Name=efficiency_p Title=efficiency_p, Long, 2 <#eta < 5 Option=
 TCanvas fXlowNDC=0 fYlowNDC=0 fWNDC=1 fHNDC=1 Name= efficiency_p Title= efficiency_p, Long, 2 <#eta < 5 Option=
  OBJ: TList	TList	Doubly linked list : 0
   TFrame  X1= -600.000000 Y1=0.000000 X2=51100.000000 Y2=1.050000
   OBJ: TMultiGraph		 : 1 at: 0x563287220c50
   OBJ: TH1D	h_numerator_notElectrons	p distribution, not e^{-} : 1 at: 0x5632879f5320
   OBJ: TH1D	h_numerator_notElectrons	p distribution, e^{-} : 1 at: 0x563287d3a6b0
   OBJ: TLegend	TPave  	X1= 25930.263182 Y1=0.318987 X2=58582.894927 Y2=0.731013
   OBJ: TLegend	TPave  	X1= 25930.263182 Y1=0.318987 X2=58582.894927 Y2=0.731013
   OBJ: TGraphAsymmErrors	EffChecker	EffChecker not e^{-} : 1 at: 0x563287d374e0
   OBJ: TGraphAsymmErrors	EffChecker	EffChecker e^{-} : 1 at: 0x563287cd4630
   Text  X=0.540000 Y=0.350000 Text=Long, 2 <#eta < 5
   TGaxis  X1=51100.000000 Y1=0.000000 X2=51100.000000 Y2=1.050000
   OBJ: TH1F	_copy	 : 1 at: 0x563287d3b260


In [ ]:
#c1.Draw()
c2.Draw()

In [203]:
data = c1.getf


Canvas Name=efficiency_p Title=efficiency_p, Long, 2 <#eta < 5 Option=
 TCanvas fXlowNDC=0 fYlowNDC=0 fWNDC=1 fHNDC=1 Name= efficiency_p Title= efficiency_p, Long, 2 <#eta < 5 Option=
  OBJ: TList	TList	Doubly linked list : 0
   TFrame  X1= -600.000000 Y1=0.000000 X2=51100.000000 Y2=1.050000
   OBJ: TMultiGraph		 : 1 at: 0x56328666c520
   OBJ: TH1D	h_numerator_notElectrons	p distribution, not e^{-} : 1 at: 0x563286cadc10
   OBJ: TH1D	h_numerator_notElectrons	p distribution, e^{-} : 1 at: 0x563286cae7c0
   OBJ: TLegend	TPave  	X1= 25930.263182 Y1=0.318987 X2=58582.894927 Y2=0.731013
   OBJ: TLegend	TPave  	X1= 25930.263182 Y1=0.318987 X2=58582.894927 Y2=0.731013
   OBJ: TGraphAsymmErrors	EffChecker	EffChecker not e^{-} : 1 at: 0x563287222b00
   OBJ: TGraphAsymmErrors	EffChecker	EffChecker e^{-} : 1 at: 0x563287b37170
   Text  X=0.540000 Y=0.350000 Text=Long, 2 <#eta < 5
   TGaxis  X1=51100.000000 Y1=0.000000 X2=51100.000000 Y2=1.050000
   OBJ: TH1F	_copy	 : 1 at: 0x563286caf970
